In [331]:
import pandas as pd
import numpy as np
from feature_engineering import two_point_haversine
from joblib import load
from geoplotting import create_geoplot
import plotly.plotly as py
import plotly.graph_objs as go
from statistics import mean
import geopandas as gpd
from folium import plugins

In [2]:
df = pd.read_pickle('boosted_dataset.pkl')

In [3]:
df.head()

c_street_number         c_street c_unit  c_city c_state c_zip_code  \
1           12200  PRATOLINA DRIVE    NaN  AUSTIN      TX      78739   
3           15302    DOROTHY DRIVE    NaN  AUSTIN      TX      78734   
4            2515        DREW LANE    NaN  AUSTIN      TX      78748   
5           15404     JOSEPH DRIVE    NaN  AUSTIN      TX      78734   
7           11203  RANCH ROAD 2222   1001  AUSTIN      TX      78730   

        g_county        lat        lon                           adj_address  \
1  Travis County  30.186914 -97.928031  12200 PRATOLINA DRIVEAUSTIN TX 78739   
3  Travis County  30.352751 -97.956798    15302 DOROTHY DRIVEAUSTIN TX 78734   
4  Travis County  30.169753 -97.833187         2515 DREW LANEAUSTIN TX 78748   
5  Travis County  30.354369 -97.957800     15404 JOSEPH DRIVEAUSTIN TX 78734   
7  Travis County  30.399156 -97.851646  11203 RANCH ROAD 2222AUSTIN TX 78730   

   dist_to_downtown  min_dist_to_transport  price_per_sqft          price  \
1         20.553532               3.156990      166.627493  499650.759637   
3         23.717263              11.432891      208.288155  732390.079922   
4         13.735147               0.719679      180.158106  605314.822569   
5         23.884909              11.240021      208.288155  727934.284355   
7         18.323480               0.736829      274.161822  826098.731716   

          sqft  bathrooms  bedrooms  price_per_bed  
1  2998.609359   3.424194         4  124912.689909  
3  3516.234899   3.961483         4  183097.519980  
4  3359.908897   3.594583         4  151328.705642  
5  3494.842441   3.848244         4  181983.571089  
7  3013.179316   3.018958         3  275366.243905

In [4]:
centroids = load('centroids.joblib')
labels = load('labels.joblib')

In [138]:
df['labels'] = labels

In [139]:
df.head()

c_street_number         c_street c_unit  c_city c_state c_zip_code  \
1           12200  PRATOLINA DRIVE    NaN  AUSTIN      TX      78739   
3           15302    DOROTHY DRIVE    NaN  AUSTIN      TX      78734   
4            2515        DREW LANE    NaN  AUSTIN      TX      78748   
5           15404     JOSEPH DRIVE    NaN  AUSTIN      TX      78734   
7           11203  RANCH ROAD 2222   1001  AUSTIN      TX      78730   

        g_county        lat        lon                           adj_address  \
1  Travis County  30.186914 -97.928031  12200 PRATOLINA DRIVEAUSTIN TX 78739   
3  Travis County  30.352751 -97.956798    15302 DOROTHY DRIVEAUSTIN TX 78734   
4  Travis County  30.169753 -97.833187         2515 DREW LANEAUSTIN TX 78748   
5  Travis County  30.354369 -97.957800     15404 JOSEPH DRIVEAUSTIN TX 78734   
7  Travis County  30.399156 -97.851646  11203 RANCH ROAD 2222AUSTIN TX 78730   

   ...  bedrooms  price_per_bed  min_centroid_dist  norm_centroid  \
1  ...         4  124912.689909           4.327475       0.305458   
3  ...         4  183097.519980           2.658506       0.187553   
4  ...         4  151328.705642           1.053468       0.074165   
5  ...         4  181983.571089           2.856996       0.201575   
7  ...         3  275366.243905           4.926577       0.347782   

   norm_transport  norm_price_per_bed  importance_ranking  mean_centroid_dist  \
1        0.451406            0.959353            1.518102           21.355493   
3        0.060945            0.935588            1.106447           21.113102   
4        0.566400            0.948563            1.657883           18.000372   
5        0.070045            0.936043            1.114680           21.237671   
7        0.565590            0.897901            1.604851           18.147531   

   norm_mean_centroid  labels  
1            0.107343       1  
3            0.109913       3  
4            0.142920      10  
5            0.108593       3  
7            0.141360      11  

[5 rows x 26 columns]

In [ ]:

for i in range(1, 16):
    df[]

In [35]:
tups = [tuple(x) for x in centroids]
subs = df[['lat', 'lon']]
tuples = [tuple(x) for x in subs.values]
min_centroid_dist = [min([two_point_haversine(centroid, address) for centroid in tups]) for address in tuples]
mean_centroid_dist = [mean([two_point_haversine(centroid, address) for centroid in tups]) for address in tuples]

In [36]:
df['min_centroid_dist'] = min_centroid_dist
df['mean_centroid_dist'] = mean_centroid_dist

In [99]:
x_min = df['min_centroid_dist'].min()
x_max = df['min_centroid_dist'].max()
df['norm_centroid'] = df['min_centroid_dist'].map(lambda x: ((x - x_min) / (x_max - x_min)))

In [265]:
x_min = df['mean_centroid_dist'].min()
x_max = df['mean_centroid_dist'].max()
df['norm_mean_centroid'] = df['mean_centroid_dist'].map(lambda x: (1 - ((x - x_min) / (x_max - x_min))))

In [266]:
x_min = df['min_dist_to_transport'].min()
x_max = df['min_dist_to_transport'].max()
df['norm_transport'] = df['min_dist_to_transport'].map(lambda x: 0.6 * (1 - ((x - x_min) / (x_max - x_min))))

In [267]:
x_min = df['price_per_bed'].min()
x_max = df['price_per_bed'].max()
df['norm_price_per_bed'] = df['price_per_bed'].map(lambda x: (1 - ((x - x_min) / (x_max - x_min))))

In [276]:
df['importance_ranking'] = df['norm_mean_centroid'] + df['norm_transport'] + df['norm_price_per_bed']

In [277]:
importance_rankings = df[['lat', 'lon', 'importance_ranking', 'labels']].sort_values(by='importance_ranking', ascending=False)

In [278]:
# selected = importance_rankings.iloc[:100]

# selected = importance_rankings[importance_rankings['labels'] == 14].iloc[:7,:]

selected = []
for i in range(1, 16):
    data = importance_rankings[importance_rankings['labels'] == i].iloc[:7, :]
    selected.append(data.values.reshape(1,-1))

selected = np.concatenate(selected, axis=1)

In [279]:
selected = selected.reshape(98,4)
selected = pd.DataFrame(selected, columns=['lat', 'lon', 'importance_ranking', 'labels'])

In [280]:
latitudes = list(selected.lat)
longitudes = list(selected.lon)

# latitudes = list(centroids[:,0])
# longitudes = list(centroids[:,1])

In [281]:
# create_geoplot(selected, sample_data=False)

In [282]:
# pk.eyJ1IjoiYXVzdGlubWFkZXJ0IiwiYSI6ImNqdWVpOG1pcDAzdDg0M3BwajlvYzBvNGwifQ.QNvTS_HgoqwLXw9ZCBTUgA

In [286]:
mapbox_access_token = 'pk.eyJ1IjoiYXVzdGlubWFkZXJ0IiwiYSI6ImNqdWVpOG1pcDAzdDg0M3BwajlvYzBvNGwifQ.QNvTS_HgoqwLXw9ZCBTUgA'

data = [
    go.Scattermapbox(
        lat=latitudes,
        lon=longitudes,
        mode='markers',
        marker=go.scattermapbox.Marker(
            size=10
        ),
        text=['Austin'],
    )
]

layout = go.Layout(
    #autosize=True,
    height=1000,
    width=1000,
    hovermode='closest',
    mapbox=go.layout.Mapbox(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=go.layout.mapbox.Center(
            lat=30.2648,
            lon=-97.7472
        ),
        pitch=0,
        zoom=9
    ),
)

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='Austin Mapbox')


In [149]:
mapbox_access_token = 'pk.eyJ1IjoiYXVzdGlubWFkZXJ0IiwiYSI6ImNqdWVpOG1pcDAzdDg0M3BwajlvYzBvNGwifQ.QNvTS_HgoqwLXw9ZCBTUgA'

data = [
    go.Scattermapbox(
        lat=latitudes,
        lon=longitudes,
        mode='markers',
        marker=go.scattermapbox.Marker(
            size=5
        ),
        text=['Austin'],
    )
]

layout = go.Layout(
    #autosize=True,
    height=1000,
    width=1000,
    hovermode='closest',
    mapbox=go.layout.Mapbox(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=go.layout.mapbox.Center(
            lat=30.2648,
            lon=-97.7472
        ),
        pitch=0,
        zoom=9.5
    ),
)

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='Austin Mapbox')


In [141]:
stops = gpd.read_file('data/Shapefiles_20-_20JANUARY_202018/Stops/Stops.shp')

In [145]:
latitudes = stops.LATITUDE
longitudes = stops.LONGITUDE

In [287]:
df.head()

c_street_number         c_street c_unit  c_city c_state c_zip_code  \
1           12200  PRATOLINA DRIVE    NaN  AUSTIN      TX      78739   
3           15302    DOROTHY DRIVE    NaN  AUSTIN      TX      78734   
4            2515        DREW LANE    NaN  AUSTIN      TX      78748   
5           15404     JOSEPH DRIVE    NaN  AUSTIN      TX      78734   
7           11203  RANCH ROAD 2222   1001  AUSTIN      TX      78730   

        g_county        lat        lon                           adj_address  \
1  Travis County  30.186914 -97.928031  12200 PRATOLINA DRIVEAUSTIN TX 78739   
3  Travis County  30.352751 -97.956798    15302 DOROTHY DRIVEAUSTIN TX 78734   
4  Travis County  30.169753 -97.833187         2515 DREW LANEAUSTIN TX 78748   
5  Travis County  30.354369 -97.957800     15404 JOSEPH DRIVEAUSTIN TX 78734   
7  Travis County  30.399156 -97.851646  11203 RANCH ROAD 2222AUSTIN TX 78730   

   ...  bedrooms  price_per_bed  min_centroid_dist  norm_centroid  \
1  ...         4  124912.689909           4.327475       0.305458   
3  ...         4  183097.519980           2.658506       0.187553   
4  ...         4  151328.705642           1.053468       0.074165   
5  ...         4  181983.571089           2.856996       0.201575   
7  ...         3  275366.243905           4.926577       0.347782   

   norm_transport  norm_price_per_bed  importance_ranking  mean_centroid_dist  \
1        0.451406            0.959353            1.947475           21.355493   
3        0.060945            0.935588            1.546100           21.113102   
4        0.566400            0.948563            2.229564           18.000372   
5        0.070045            0.936043            1.549051           21.237671   
7        0.565590            0.897901            2.170290           18.147531   

   norm_mean_centroid  labels  
1            0.536716       1  
3            0.549567       3  
4            0.714601      10  
5            0.542963       3  
7            0.706799      11  

[5 rows x 26 columns]

In [288]:
print(df['lat'].max(), df['lat'].min(), df['lon'].max(), df['lon'].min())

30.500168300000002 30.059266100000002 -97.5078501 -97.999424


In [324]:
zips = gpd.read_file("/Users/austinmadert/galvanize_repositories/real_estate_opportunity_lih/data/cb_2017_us_zcta510_500k")  
zips.crs = {'datum': 'NAD83', 'ellps': 'GRS80', 'proj':'longlat'}

austin = zips[ zips['ZCTA5CE10'].isin(aus_zip_codes)]

# convert it to the projection of our folium openstreetmap  
austin = austin.to_crs({'init':'epsg:4326'})

In [326]:
import folium
from folium.plugins import HeatMap

max_amount = float(df['price'].max())

hmap = folium.Map(location=[30.2648, -97.7472], zoom_start=7, )

hm_wide = HeatMap( list(zip(df.lat.values, df.lon.values, df.price.values)),
                   min_opacity=0.2,
                   max_val=max_amount,
                   radius=17, blur=15, 
                   max_zoom=1, 
                 )

folium.GeoJson(austin).add_to(hmap)
hmap.add_child(hm_wide)

In [291]:
zips = gpd.read_file("/Users/austinmadert/galvanize_repositories/real_estate_opportunity_lih/data/cb_2017_us_zcta510_500k")  
zips.head()

ZCTA5CE10      AFFGEOID10 GEOID10     ALAND10  AWATER10  \
0     35442  8600000US35442   35442   610213891  10838694   
1     85365  8600000US85365   85365  3545016067   9766486   
2     71973  8600000US71973   71973   204670474   1264709   
3     95445  8600000US95445   95445   221559097   7363179   
4     06870  8600000US06870   06870     5945321   3841130   

                                            geometry  
0  (POLYGON ((-88.252618 32.92675, -88.249724 32....  
1  (POLYGON ((-114.684663 32.687389, -114.676063 ...  
2  POLYGON ((-94.46643176650841 34.330735, -94.46...  
3  POLYGON ((-123.643051 38.851233, -123.641401 3...  
4  POLYGON ((-73.58765810889219 41.0076522198727,...

In [292]:
from src import data_items

In [293]:
aus_zip_codes = set(data_items.zip_latlong)

In [321]:
aus_zip_codes = set(str(x) for x in aus_zip_codes)

In [317]:
austin = zips[ zips['ZCTA5CE10'].isin(aus_zip_codes)]

In [323]:
aus_zip_codes

{'73301',
 '73344',
 '78701',
 '78702',
 '78703',
 '78704',
 '78705',
 '78708',
 '78709',
 '78710',
 '78711',
 '78712',
 '78713',
 '78714',
 '78715',
 '78716',
 '78717',
 '78718',
 '78719',
 '78720',
 '78721',
 '78722',
 '78723',
 '78724',
 '78725',
 '78726',
 '78727',
 '78728',
 '78729',
 '78730',
 '78731',
 '78732',
 '78733',
 '78734',
 '78735',
 '78736',
 '78737',
 '78738',
 '78739',
 '78741',
 '78742',
 '78744',
 '78745',
 '78746',
 '78747',
 '78748',
 '78749',
 '78750',
 '78751',
 '78752',
 '78753',
 '78754',
 '78755',
 '78756',
 '78757',
 '78758',
 '78759',
 '78760',
 '78761',
 '78762',
 '78763',
 '78764',
 '78765',
 '78766',
 '78767',
 '78768',
 '78769',
 '78772',
 '78773',
 '78774',
 '78778',
 '78779',
 '78780',
 '78781',
 '78783',
 '78785',
 '78789',
 '78799'}

In [320]:
zips.ZCTA5CE10[0]

'35442'

In [328]:
m = folium.Map([30.2648, -97.7472], zoom_start=11)
m

In [329]:
for index, row in df.iterrows():
    folium.CircleMarker([row['lat'], row['lon']],
                        radius=15,
                        popup=row['adj_address'],
                        fill_color="#3db7e4",
                       ).add_to(m)

In [ ]:
# convert to (n, 2) nd-array format for heatmap
arr = df[['lat', 'lon']].as_matrix()

# plot heatmap
m.add_children(plugins.HeatMap(arr, radius=15))
m